In [1]:
"""
Poisson leap process
"""

"Poisson leap process\n"

In [2]:
using Distributed

In [3]:
length(Sys.cpu_info())
addprocs(4) ;

In [4]:
@everywhere using Random, Distributions, Plots, DelimitedFiles

In [5]:
@everywhere struct SPN
    init::Vector{Real}
    k::Vector{Real}
    S::Array{Real}
    Tmax::Real
    dt::Real
    function SPN(init, k, S, Tmax, dt)
        new(Float64.(init), Float64.(k), Float64.(S), Float64.(Tmax), Float64.(dt))
    end
end

In [6]:
@everywhere init(N::SPN) = Float64.(N.init)
@everywhere rates(N::SPN) = Float64.(N.k)
@everywhere StoiMat(N::SPN) = Float64.(N.S)
@everywhere Tmax(N::SPN) = Float64.(N.Tmax)
@everywhere dt(N::SPN) = Float64.(N.dt)

In [26]:
@everywhere function hazzy(x::Vector{Float64}, th::Vector{Float64})
    return [x[1], x[2], x[1], x[2], x[1]].*th[1:5]
end

In [8]:
@everywhere const post = [[2,0,0,0,1] [0,2,0,0,1]]
@everywhere const pre = [[1,0,1,0,1] [0,1,0,1,0]]
@everywhere const SS = post - pre
@everywhere const kk = [3.06e-8, 3.06e-8, 3.06e-8, 3.06e-8, 0.0, 8.99e-9, 2e-3];

In [9]:
@everywhere function gen_inits(μ::Real, σ::Real, α::Real, β::Real)::Vector{Float64}
    CC = rand(Normal(μ, σ))
    hh = rand(Beta(α, β))
    return round.( [CC*(1-hh), CC*hh] )
end

In [73]:
@everywhere function transform_summ(popdym)::Array{Union{Float64, Missing}}
    copy_num = popdym[:,1] .+ popdym[:,2]
    
    mut_load = Array{Union{Float64, Missing}}(undef, length(copy_num))
    idx = copy_num .!= 0.0
    mut_load[.!idx] .= missing
    mut_load[idx] .=  popdym[idx,2] ./ copy_num[idx]
    
    return hcat(copy_num, mut_load)
end

In [134]:
@everywhere function tauleap(N::SPN, Tmax::Real, dt::Real)::Array{Union{Float64, Missing}}
    c = k(N)
    nn = n(N)
    SS = S(N)
    
    xmat = Array{Float64}(undef, 2,nn+1)
    xmat[:,1] = init(N)
    i = 1
    while i<nn
        h = hazzy(xmat[:,i], c)
        if( sum(h)<1e-10 )
            xmat[:,(i+1:nn)] = zeros(2, nn-i)
            return transform_summ(xmat')
        end
        R = randPois(h*step)
        xmat[:,i+1] = xmat[:,i] + (SS'*R) 
        i += 1
    end
    return transform_summ(xmat')
end


In [12]:
@everywhere function randPois(λ::Vector{Float64})::Vector{Int64}
    pos_rates = (λ.>0).*λ
    [rand(Poisson(rate)) for rate in pos_rates]
end

In [13]:
hour = 3600
day = 24*hour
year = 365*day

Nsim = 1000
step = day
T_max = 80*year ; 

In [135]:
Ntest = SPN([100,100], kk, SS, T_max, step)
@time  tauleap(Ntest)
"""
a single runs takes ~0.04 seconds
"""


  0.053964 seconds (437.03 k allocations: 39.958 MiB)


"a single runs takes ~0.04 seconds\n"

In [15]:
"""
sim_single = Array{Float64}(undef, n(Ntest), 2,Nsim)
@time for i=1:Nsim
    sim_single[:,:,i] = tauleap(Ntest)
end
1000 simulations takes ~21 seconds
"""

"sim_single = Array{Float64}(undef, n(Ntest), 2,Nsim)\n@time for i=1:Nsim\n    sim_single[:,:,i] = tauleap(Ntest)\nend\n1000 simulations takes ~21 seconds\n"

In [115]:
# The arguments are: 1) a function 'f' and 2) a list with the input.
@everywhere function par_map(Nsim, f, SPN)
    np = nworkers()            # Number of processes available.
    nn = n(SPN) # dimension for output
    output = Vector{Array{Union{Float64, Missing}, 2}}(undef, Nsim) # Where we will write the results. As we do not know
                             # the type (Integer, Tuple...) we write "Any"
    i = 1
    nextidx() = (idx = i; i += 1; idx) # Function to know which is the next work item.
                                       # In this case it is just an index.
    @sync begin #@sync: must complete all jobs in block
        for p = 1:np # loops through all processes (workers)
            if p != myid() || np == 1 # first worker used only if all others are busy 
                @async begin # launch several tasks simultaneaously
                    while true
                        idx = nextidx()
                        if idx > Nsim
                            break
                        end
                        output[idx] = remotecall_fetch(f, p, SPN)
                    end
                end
            end
        end
    end
    output
end

In [136]:
@time simulations = simulation_map(Nsim, tauleap, Ntest) ;
"""
simple simulation: 15 seconds
workers = 4
time step = 1 day
"""

 14.514985 seconds (174.15 M allocations: 3.330 GiB, 2.86% gc time)


"simple simulation: 30 seconds\nworkers = 4\ntime step = 1 day\n\n\n"

In [140]:
simulations

1000-element Vector{Array{Union{Missing, Float64}, N} where N}:
 [200.0 0.5; 200.0 0.5; … ; 257.0 0.0; 10.0 0.5]
 [200.0 0.5; 200.0 0.5; … ; 189.0 1.0; 312.0 0.0]
 [200.0 0.5; 202.0 0.504950495049505; … ; 0.0 missing; 159.0 0.0]
 [200.0 0.5; 200.0 0.5; … ; 95.0 0.0; 51.0 1.0]
 [200.0 0.5; 200.0 0.5; … ; 41.0 1.0; 554.0 0.5]
 [200.0 0.5; 200.0 0.5; … ; 0.0 missing; 411.0 0.2749391727493917]
 [200.0 0.5; 200.0 0.495; … ; 158.0 0.0; 1.9615384615384615 0.5]
 [200.0 0.5; 199.0 0.49748743718592964; … ; 385.0 0.7766233766233767; 0.0 missing]
 [200.0 0.5; 200.0 0.5; … ; 228.0 1.0; 18.0 0.5]
 [200.0 0.5; 201.0 0.5074626865671642; … ; 491.0 0.5641547861507128; 382.0 0.5]
 [200.0 0.5; 198.0 0.494949494949495; … ; 226.0 0.41150442477876104; 44.0 0.5]
 [200.0 0.5; 200.0 0.505; … ; 0.0 missing; 10.0 0.5]
 [200.0 0.5; 200.0 0.5; … ; 114.0 0.05263157894736842; 0.0 missing]
 ⋮
 [200.0 0.5; 203.0 0.4975369458128079; … ; 96.0 0.6354166666666666; 602.0 0.5]
 [200.0 0.5; 200.0 0.5; … ; 319.0 0.752351097178

In [124]:
@everywhere function quantiles(sims, p)
    """
    returns quantile summaries from simulations
    """
    Nsim = length(sims) # Nsim: number of simulations
    n = size(sims[1])[1] # length of one simulation
    out = Array{Float64}(undef, n,length(p),2)
    for t=1:n
        out[t,:,1] = quantile(skipmissing([sims[i][t,1] for i=1:Nsim]), p)
        out[t,:,2] = quantile(skipmissing([sims[i][t,2] for i=1:Nsim]), p)
    end
    out
end

In [20]:
#writedlm("Simulations/CN_qnt_tau_jl.txt", )

In [137]:
sims_qntl = quantiles(simulations, [0.025,0.25,0.5,0.75,0.975]) ;

In [126]:
myBlack = colorant"rgb(0,0,0,0.1)"
ts = [0:step:T_max;]./year;

In [139]:
p3 = plot(ts, sims_qntl[:,:,1], title="Copy Number Quantiles")
p4 = plot(ts, sims_qntl[:,:,2], title="Mutation Load Quantiles")
plot(p3, p4, layout=(1,2), legend=false)

In [95]:
writedlm("Simulations/CN_qnt_tau_jl.txt", sims_qntl[:,:,1])
writedlm("Simulations/ML_qnt_tau_jl.txt", sims_qntl[:,:,2]) ;

In [103]:
function distributions_t(sims, t, Tmax, dt)
    t_tot = [dt:dt:Tmax;]
    Nsim = length(sims)
    nt = length(t)
    sim_t = Array{Float64}(undef, Nsim,nt,2)
    for i=1:Nsim
        for j=1:nt
            sim_t[i,j,1] = sims[i][findall(x->x==t[j], t_tot),1][1]
            sim_t[i,j,2] = sims[i][findall(x->x==t[j], t_tot),2][1]
        end
    end
    return sim_t
end

distributions_t (generic function with 1 method)

In [105]:
dist_sims = distributions_t(simulations, [10:10:80;]*year, T_max, step) ; 

LoadError: MethodError: [0mCannot `convert` an object of type [92mMissing[39m[0m to an object of type [91mFloat64[39m
[0mClosest candidates are:
[0m  convert(::Type{T}, [91m::T[39m) where T<:Number at number.jl:6
[0m  convert(::Type{T}, [91m::Number[39m) where T<:Number at number.jl:7
[0m  convert(::Type{T}, [91m::Base.TwicePrecision[39m) where T<:Number at twiceprecision.jl:250
[0m  ...

In [25]:
writedlm("Simulations/CN_ts_tau_jl.txt", dist_sims[:,:,1])
writedlm("Simulations/ML_ts_tau_jl.txt", dist_sims[:,:,2]) ;

LoadError: UndefVarError: dist_sims not defined